## En este notebook aprenderás a crear una red neuronal desde cero:
<div style="background-color: rgb(0, 143, 88);margin: 20px; padding: 20px; border-left: 9px solid #ffb200;">
<ul style="color: rgb(255, 255, 255);font-weight:bold;font-size:15px;">
Para la creación de la red se desarrollarán distintas funciones:
    <li style="padding:10px;">Funciones de activación (Sigmoid y ReLu). </li>
    <li style="padding:10px;">Función para evaluar cada capa (función de coste 'Mean Squared Error')</li>
    <li style="padding:10px;">Función para el entrenamiento de la red.</li>
    <li style="padding:10px;">Creación de la clase 'layer' para poder montar una red neuronal.</li>
    <li style="padding:10px;">Para terminar, visualizaremos como entrena nuestro modelo guardando los datos (predicción y error) en cada iteración.</li>
</ul>
</div>

A continuación, desarrollaremos cada parte mencionada en el punto anterior con explicaciones más detalladas.

# Funciones de activación

## Sigmoid

Creamos la función de activación **sigmoid**. La función sigmoide ***recibe un valor x y devuelve un valor entre 0 y 1***. Esto hace que sea una función muy interesante, ya que indica la probabilidad. Por ejemplo, si usamos la función sigmoide en la última capa para un modelo de clasificación entre dos clases, la función devolverá la probabilidad de pertenecer a una clase.

Tras la creación de la función apreciamos gráficamente su comportamiento.

In [ ]:
import numpy as np
import math
import matplotlib.pyplot as plt

#Función sigmoid
sigmoid = (
  lambda x:1 / (1 + np.exp(-x)),
  lambda x:x * (1 - x)
  )

#datos para los graficos
rang = np.linspace(-10,10).reshape([50,1])
datosSigmoid = sigmoid[0](rang)
datosSigmoidDerivada = sigmoid[1](rang)

#visualizar los graficos
fig, axes = plt.subplots(nrows=1, ncols=2, figsize =(15,5))
axes[0].plot(rang, datosSigmoid)
axes[1].plot(rang, datosSigmoidDerivada)
fig.tight_layout()

## ReLu

Creamos la función de activación ***ReLu***. El comportamiento de esta función es muy simple, ***para valores negativos, la función devuelve cero. Para valores positivos, la función devuelve el mismo valor***. Pero, a pesar de ser tan simple, esta función es la función de activación más usada en el campo de las redes neuronales y deep learning. 

Tras la creación de la función apreciamos gráficamente su comportamiento.


In [ ]:
def derivada_relu(x):
    x[x<=0] = 0
    x[x>0] = 1
    return x
##########################
relu = (
  lambda x: x * (x > 0),
  lambda x:derivada_relu(x)
  )

#datos para los graficos
datosRelu = relu[0](rang)
datosReluDerivada = relu[1](rang)

# Volvemos a definir rango que ha sido cambiado
rang = np.linspace(-10,10).reshape([50,1])

# Cremos los graficos
fig, axes = plt.subplots(nrows=1, ncols=2, figsize =(15,5))
axes[0].plot(rang, datosRelu[:,0])
axes[1].plot(rang, datosReluDerivada[:,0])
plt.show()

# Función de coste

## Mean Squared Error

Para entrenar la red neuronal una de las cosas que debemos hacer es calcular cuánto ha fallado. Para esto, usaremos uno de los estimadores más típicos, el error cuadrático medio (MSE).

El error cuadrático medio se calcula de la siguiente manera: a cada valor de la predicción se le resta el valor real, se eleva al cuadrado, se hace la suma ponderada y se calcula su raíz. 
Además, aprovecharemos para que esta función nos devuelva la derivada de la función de coste, la cual la utilizaremos en el paso de backpropagation.

In [ ]:
def mse(Ypred, Y):
    
    # Calculo del error
    x = (np.array(Ypred) - np.array(Y)) ** 2
    x = np.mean(x)

    # Calculo de la derivada de la funcion
    y = np.array(Ypred) - np.array(Y)
    return (x,y)

# Entrenamiento de la red neuronal

Para poder entender el funcionamiento de esta función se explicará paso a paso las partes más importantes del código. Leer los comentarios del código también te ayudará mucho en el aprendizaje.

Estos son los pasos más importantes y sus respectivas explicaciones:

***PASO 1:***
**Predicción de la red neuronal**.
Para que la red neuronal prediga, estos son los cálculos a seguir: multiplicar los valores de entrada con la matriz de pesos W, sumarlo con el parámetro bias (b) y aplicar la función de activación.

***PASO 2:***
**Predicción de la red neuronal**
Para poder calcular el descenso del gradiente necesitamos las derivadas de la función de coste. Por esta razón, al definir las funciones de activación hemos definido también sus derivadas.

En cada ronda estos valores se irán cambiando. Lo primero que debemos hacer es transmitir el error hacia atrás. Como estamos trabajando de atrás hacia adelante, empezaremos de la última capa.

Este error, se calcula como la derivada de la función de coste sobre el resultado de la capa siguiente por la derivada de la función de activación.

***PASO 3:***
**Optimización de los parametros**
Después de propagar el error entre las capas, hay que optimizar los valores de los parámetros con esos errores mediante *Gradient Descent*. Para esto, hay que restarle al valor anterior de b y W, las derivadas en el punto de los parámetros b y W.

In [ ]:
def entrenamiento(X,Y, red_neuronal, lr = 0.01):
    
# PASO 1

  # Output guarda el resultado de cada capa
  # capa 1, el resultado es el valor de entrada, es decir, X
    output = [X]

    for capa in range(len(red_neuronal)):  
        #multiplicar los valores de la entrada con la matriz de pesos y sumarlo con el bias
        a = output[-1] @ red_neuronal[capa].W + red_neuronal[capa].b # @ para la multiplicación matricial

        b = red_neuronal[capa].funcion[0](a) #aplicar funcion de activacion

        # Incluimos el resultado de la capa a output
        output.append(b)

# PASO 2
    
  # Backpropagation

    backprop = list(range(len(output)-1))
    backprop.reverse()

  # Guardar el error de la capa
    delta = []

  # Backpropagation
    for capa in backprop:

        b = output[capa+1]

        #Backpropagation en la última capa
        if capa == backprop[0]:
            mserror = mse(b,Y)[1] * red_neuronal[capa].funcion[1](b)
            delta.append(mserror)
        #Backpropagation en las capas restantes
        else:
            mserror = delta[-1] @ W_temp * red_neuronal[capa].funcion[1](b)
            delta.append(mserror)
        #Guardar los valores del peso
        W_temp = red_neuronal[capa].W.transpose()

# PASO 3    
    
        # Gradient Descent para optimizar los valores de los parametros en cada capa
        red_neuronal[capa].b = red_neuronal[capa].b - np.mean(delta[-1], axis = 0, keepdims = True) * lr
        red_neuronal[capa].W = red_neuronal[capa].W - output[capa].transpose() @ delta[-1] * lr

    return output[-1]

# Creación de las capas 

Para crear la estructura vamos a definir una clase llamada layer. A continuación, inicializaremos los parámetros b y W con datos aleatorios. Para esto utilizaremos la función *trunconorm* de la librería *stats*, ya que esto nos permite crear datos aleatorios dado un rango, media y desviación estándar.

Para seguir con el desarrollo hay que definir tres cosas: el número de capas de la red, el número de neuronas en cada capa y la función de activación en cada capa.

Para finalizar, se crea la estructura de la red neuronal. Esto, se hace de forma iterativa y se ira guardando esta estructura en un nuevo objeto, llamado red_neuronal.

In [ ]:
from scipy import stats

class layer():
    def __init__(self, neuronas_capa_anterior, neuronas, funcion):
        self.funcion = funcion
        self.b  = np.round(stats.truncnorm.rvs(-1, 1, loc=0, scale=1, size= neuronas).reshape(1,neuronas),3)
        self.W  = np.round(stats.truncnorm.rvs(-1, 1, loc=0, scale=1, size= neuronas * neuronas_capa_anterior).reshape(neuronas_capa_anterior,neuronas),3)

# 8 neuronas para la capa de entrada, 16 y 32 neuronas para las dos capas ocultas, 1 neurona para la capa de salida
neuronas_capa = [8,16,32,1]
#Funciones de activación para cada capa (en la primera capa no se aplica ninguna función)
funciones = [relu,relu, sigmoid] 
red_neuronal = []

# Creando la estructura de la red
for capa in list(range(len(neuronas_capa)-1)):
    x = layer(neuronas_capa[capa],neuronas_capa[capa+1],funciones[capa])
    red_neuronal.append(x)   

# Creación de datos aleatorios para entrenamiento de la red

In [ ]:
from random import shuffle

np.random.seed(0)

X =  np.round(np.random.randn(40,8),3) # Ejemplo de datos de entrada

Y = [0] * 20 + [1] * 20
shuffle(Y)
Y = np.array(Y).reshape(len(Y),1)

# Visualización del entrenamiento de nuestra red

Una vez que ya tenemos definida la red, llamaremos a la función de entrenamiento y guardaremos los resultados de las predicciones y de los errores. Con esto, luego visualizamos en un gráfico como ha entrenado nuestra red.

In [ ]:
error = []
pred = []

for epoch in range(0,1000):
    predict = entrenamiento(X = X ,Y = Y ,red_neuronal = red_neuronal, lr = 0.001)
    pred.append(predict)
    mserror = mse(np.round(pred[-1]),Y)[0]
    error.append(mserror)

In [ ]:
epoch = list(range(0,1000))
plt.plot(epoch, error)

Se aprecia en el gráfico como nuestra red neuronal ha entrenado y como va mejorando el error del entrenamiento, hasta que llegados a un punto, la red ya no mejora más los resultados.

# Conclusión

Como bien has visto no es tarea sencilla crear una red neuronal simple, pero no te preocupes, ya que si te toca trabajar con redes neuronales usaras librerías como Tensorflow o Keras.

Este módulo sirve para interiorizar y entender el funcionamiento interno de una red neuronal. Espero que te haya ayudado y te sirva como aprendizaje.

Suerte en tu formación!😊😊